<center>

## [S. Mussard](https://sites.google.com/view/cv-stphane-mussard/accueil "Homepage")

# UM6P

# Natural Language Processing: LOGIT


<center> <a href="https://www.fgses-um6p.ma/"><img src="UM6P.png",style="float: left; max-width: 500px; width: 20" />



<div align="center"> 
<a href="https://scikit-learn.org/stable/modules/generated/sklearn.feature_extraction.text.TfidfVectorizer.html"><img src="http://scikit-learn.org/stable/_static/scikit-learn-logo-small.png" style="max-width: 180px; display: inline" alt="Scikit-Learn"/></a>
</div>
<div align="center"> <a href="https://www.python.org/"><img src="https://upload.wikimedia.org/wikipedia/commons/thumb/f/f8/Python_logo_and_wordmark.svg/390px-Python_logo_and_wordmark.svg.png" style="max-width: 150px; display: inline" alt="Python"/></a> 
</div>
    


<div align="center">

## Sentiment Analysis

In [1]:
# Importation  

%matplotlib inline 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from sklearn import metrics
import torch
from torch.utils.data import Dataset, DataLoader
from transformers import AutoModel, AutoTokenizer
from transformers import AutoModelForSequenceClassification, AutoTokenizer

import gradio as gr
from gradio.components import Label

In [5]:
path = "./weights"
model = AutoModel.from_pretrained(path, trust_remote_code=True)
class CamembertClass(torch.nn.Module):
    def __init__(self):
        super(CamembertClass, self).__init__()
        self.l1 = model
        self.dropout = torch.nn.Dropout(0.1)
        self.pre_classifier = torch.nn.Linear(1024, 1024)
        self.classifier = torch.nn.Linear(1024, 3)

    def forward(self, input_ids, attention_mask, token_type_ids):
        output_1 = self.l1(input_ids=input_ids, attention_mask=attention_mask, token_type_ids=token_type_ids)
        hidden_state = output_1[0]
        pooler = hidden_state[:, 0]
        pooler = self.pre_classifier(pooler)
        pooler = torch.nn.ReLU()(pooler)
        pooler = self.dropout(pooler)
        output = self.classifier(pooler)
        return output

Some weights of the model checkpoint at ./poids were not used when initializing RobertaModel: ['classifier.out_proj.weight', 'classifier.dense.bias', 'classifier.out_proj.bias', 'classifier.dense.weight']
- This IS expected if you are initializing RobertaModel from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing RobertaModel from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of RobertaModel were not initialized from the model checkpoint at ./poids and are newly initialized: ['roberta.pooler.dense.weight', 'roberta.pooler.dense.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [6]:
#model_gradio = CamembertClass()
path = "./pytorch_model.bin"
model = torch.load(path, map_location="cpu")
path_tokenizer = "./"
tokenizer = AutoTokenizer.from_pretrained(path_tokenizer)


In [4]:
#pip install pydantic==1.10.7

In [7]:
model.eval()  # Mettez votre modèle en mode évaluation

# Fonction d'inférence pour Gradio
def predict(text):
    inputs = tokenizer(text, return_tensors="pt", padding=True, truncation=True, max_length=512)
    
    # Extract necessary inputs for the model
    input_ids = inputs['input_ids']
    attention_mask = inputs['attention_mask']
    token_type_ids = inputs.get('token_type_ids', None)  # Some models do not use segment IDs
    
    # Make prediction
    with torch.no_grad():
    # Directly use outputs if your model returns logits directly
        logits = model(input_ids=input_ids, attention_mask=attention_mask, token_type_ids=token_type_ids)

 
    # Convert logits to probabilities
    probabilities = torch.softmax(logits, dim=1).detach().cpu().numpy()[0]
    # Replace the following with your actual classes
    classes = ['Negative Sentiment', 'Positive Sentiment']
    return {classes[i]: float(probabilities[i]) for i in range(len(classes))}

# Création de l'interface Gradio
iface = gr.Interface(fn=predict,
                     inputs=gr.components.Textbox(placeholder="Enter your text here..."),
                     outputs=gr.components.Label(num_top_classes=2))
iface.launch(share=True)


Running on local URL:  http://127.0.0.1:7860
Running on public URL: https://93ecddda8853b625c0.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)
